## Aprendizaje de reglas de asociación

Objetivo:
    
    derivar reglas de la forma {A} -> {B}
    

In [1]:
import numpy as np
from itertools import combinations, groupby
from collections import Counter
import pandas as pd

### Cargar datos

In [2]:
pd.set_option('display.max_columns', 9720)
pd.set_option('display.max_rows', 29)
movies_df = pd.read_csv('data/movies.csv')
raitings_df = pd.read_csv('data/ratings.csv') 
tags_df = pd.read_csv('data/tags.csv') 


In [3]:
movies_df.head()

movieId                               title  \
0        1                    Toy Story (1995)   
1        2                      Jumanji (1995)   
2        3             Grumpier Old Men (1995)   
3        4            Waiting to Exhale (1995)   
4        5  Father of the Bride Part II (1995)   

                                        genres  
0  Adventure|Animation|Children|Comedy|Fantasy  
1                   Adventure|Children|Fantasy  
2                               Comedy|Romance  
3                         Comedy|Drama|Romance  
4                                       Comedy

In [4]:
movies_df.dtypes

movieId     int64
title      object
genres     object
dtype: object

In [5]:
movies_df.shape

(9742, 3)

In [6]:
raitings_df.head()

userId  movieId  rating  timestamp
0       1        1     4.0  964982703
1       1        3     4.0  964981247
2       1        6     4.0  964982224
3       1       47     5.0  964983815
4       1       50     5.0  964982931

In [7]:
raitings_df.dtypes

userId         int64
movieId        int64
rating       float64
timestamp      int64
dtype: object

In [8]:
raitings_df.shape

(100836, 4)

In [9]:
tags_df.head()

userId  movieId              tag   timestamp
0       2    60756            funny  1445714994
1       2    60756  Highly quotable  1445714996
2       2    60756     will ferrell  1445714992
3       2    89774     Boxing story  1445715207
4       2    89774              MMA  1445715200

In [10]:

tags_df.groupby(['tag']).size().sort_values()

tag
"artsy"                1
falling                1
fairy tale             1
faerie tale            1
exciting               1
                    ... 
surreal               23
superhero             24
thought-provoking     24
atmospheric           36
In Netflix queue     131
Length: 1589, dtype: int64

In [11]:
tags_df.dtypes

userId        int64
movieId       int64
tag          object
timestamp     int64
dtype: object

### Preparación de datos

In [12]:
df = pd.merge(raitings_df,movies_df, on='movieId')
df.head()
df.shape

(100836, 6)

In [13]:
df.groupby(['movieId','userId']).size().sort_values(ascending=False)

movieId  userId
193609   331       1
1615     45        1
         140       1
         195       1
         217       1
                  ..
5445     434       1
         438       1
         448       1
         453       1
1        1         1
Length: 100836, dtype: int64

### Análisis de datos

In [23]:
grouped = df[df.rating==5].groupby('userId')[['userId','title','rating','movieId','genres']]

grouped.get_group(4).sort_values('title')

userId                                             title  rating  \
21229       4                               12 Angry Men (1957)     5.0   
21988       4                                  Afterglow (1997)     5.0   
23309       4                                  Airplane! (1980)     5.0   
23482       4  All About My Mother (Todo sobre mi madre) (1999)     5.0   
13850       4                            American Beauty (1999)     5.0   
...       ...                                               ...     ...   
21148       4                          Strictly Ballroom (1992)     5.0   
24404       4                                    Traffic (2000)     5.0   
21797       4                        Waiting for Guffman (1996)     5.0   
22254       4                            West Side Story (1961)     5.0   
5549        4                          Wizard of Oz, The (1939)     5.0   

       movieId                              genres  
21229     1203                               Drama  
21988     1733                       Drama|Romance  
23309     2791                              Comedy  
23482     3083                               Drama  
13850     2858                       Drama|Romance  
...        ...                                 ...  
21148     1188                      Comedy|Romance  
24404     4034                Crime|Drama|Thriller  
21797     1449                              Comedy  
22254     1947               Drama|Musical|Romance  
5549       919  Adventure|Children|Fantasy|Musical  

[64 rows x 5 columns]

### Reglas de Asociación basado en peliculas

- Item: Peliculas vistas por un usuario
- I: todas las peliculas vistas por los usuarios
- Transacción: peliculas vistas por cada usuario

In [14]:
peliculas_df = df.sort_values( by='userId', axis=0, ascending=True, inplace=False, kind='quicksort', na_position='last')
display(peliculas_df.head())
peliculas=peliculas_df.values[:,[0,4]]
print(peliculas)

userId  movieId  rating  timestamp                       title  \
0           1        1     4.0  964982703            Toy Story (1995)   
12117       1     2389     2.0  964983094               Psycho (1998)   
12126       1     2395     5.0  964981093             Rushmore (1998)   
12182       1     2406     4.0  964982310  Romancing the Stone (1984)   
776         1       70     3.0  964982400  From Dusk Till Dawn (1996)   

                                            genres  
0      Adventure|Animation|Children|Comedy|Fantasy  
12117                        Crime|Horror|Thriller  
12126                                 Comedy|Drama  
12182              Action|Adventure|Comedy|Romance  
776                  Action|Comedy|Horror|Thriller

[[1 'Toy Story (1995)']
 [1 'Psycho (1998)']
 [1 'Rushmore (1998)']
 ...
 [610 'Coraline (2009)']
 [610 'Serious Man, A (2009)']
 [610 '31 (2016)']]


In [19]:
dummyes_mov = pd.get_dummies(peliculas_df[['userId','title']])
dummyes_mov = dummyes_mov.groupby('userId').sum()
dummyes_mov.head()

title_'71 (2014)  title_'Hellboy': The Seeds of Creation (2004)  \
userId                                                                    
1                      0                                              0   
2                      0                                              0   
3                      0                                              0   
4                      0                                              0   
5                      0                                              0   

        title_'Round Midnight (1986)  title_'Salem's Lot (2004)  \
userId                                                            
1                                  0                          0   
2                                  0                          0   
3                                  0                          0   
4                                  0                          0   
5                                  0                          0   

        title_'Til There Was You (1997)  \
userId                                    
1                                     0   
2                                     0   
3                                     0   
4                                     0   
5                                     0   

        title_'Tis the Season for Love (2015)  title_'burbs, The (1989)  \
userId                                                                    
1                                           0                         0   
2                                           0                         0   
3                                           0                         0   
4                                           0                         0   
5                                           0                         0   

        title_'night Mother (1986)  title_(500) Days of Summer (2009)  \
userId                                                                  
1                                0                                  0   
2                                0                                  0   
3                                0                                  0   
4                                0                                  0   
5                                0                                  0   

        title_*batteries not included (1987)  title_...All the Marbles (1981)  \
userId                                                                          
1                                          0                                0   
2                                          0                                0   
3                                          0                                0   
4                                          0                                0   
5                                          0                                0   

        title_...And Justice for All (1979)  \
userId                                        
1                                         0   
2                                         0   
3                                         0   
4                                         0   
5                                         0   

        title_00 Schneider - Jagd auf Nihil Baxter (1994)  \
userId                                                      
1                                                       0   
2                                                       0   
3                                                       0   
4                                                       0   
5                                                       0   

        title_1-900 (06) (1994)  title_10 (1979)  title_10 Cent Pistol (2015)  \
userId                                                                          
1                             0                0                            0   
2                             0                0                            0   
3                     

In [31]:
def clean_dataset(df):
    lista = []
    for col in df.columns:
        if len(df.index[df[col] == 2].tolist())!=0:
            lista.append(df.index[df[col] == 2])
    index_list = []
    for each in lista:
        for a in each:
            index_list.append(a)
    index_list
    return df.drop(index_list)



In [ ]:
dummyes_mov = clean_dataset(dummyes_mov)

In [21]:
from mlxtend.frequent_patterns import apriori

frequent_itemsets = apriori(dummyes_mov, min_support=0.09, use_colnames=True)
frequent_itemsets['length'] = frequent_itemsets['itemsets'].apply(lambda x: len(x))
frequent_itemsets

support                                           itemsets  length
0       0.094059                        (title_12 Angry Men (1957))       1
1       0.176568               (title_2001: A Space Odyssey (1968))       1
2       0.092409                       (title_28 Days Later (2002))       1
3       0.125413                                 (title_300 (2007))       1
4       0.117162             (title_40-Year-Old Virgin, The (2005))       1
...          ...                                                ...     ...
274786  0.092409  (title_Jurassic Park (1993), title_Forrest Gum...      10
274787  0.090759  (title_Jurassic Park (1993), title_Forrest Gum...      10
274788  0.090759  (title_Forrest Gump (1994), title_Matrix, The ...      10
274789  0.090759  (title_Forrest Gump (1994), title_Toy Story (1...      10
274790  0.090759  (title_Jurassic Park (1993), title_Sixth Sense...      10

[274791 rows x 3 columns]

In [22]:
from mlxtend.frequent_patterns import association_rules

association_rules(frequent_itemsets, metric="confidence", min_threshold=0.1)

antecedents  \
0                      (title_2001: A Space Odyssey (1968))   
1                                      (title_Alien (1979))   
2                      (title_2001: A Space Odyssey (1968))   
3                                     (title_Aliens (1986))   
4                            (title_American Beauty (1999))   
...                                                     ...   
10859721  (title_Star Wars: Episode VI - Return of the J...   
10859722                        (title_Pulp Fiction (1994))   
10859723  (title_Star Wars: Episode V - The Empire Strik...   
10859724  (title_Star Wars: Episode IV - A New Hope (1977))   
10859725                     (title_Terminator, The (1984))   

                                                consequents  \
0                                      (title_Alien (1979))   
1                      (title_2001: A Space Odyssey (1968))   
2                                     (title_Aliens (1986))   
3                      (title_2001: A Space Odyssey (1968))   
4                      (title_2001: A Space Odyssey (1968))   
...                                                     ...   
10859721  (title_Jurassic Park (1993), title_Sixth Sense...   
10859722  (title_Jurassic Park (1993), title_Sixth Sense...   
10859723  (title_Jurassic Park (1993), title_Sixth Sense...   
10859724  (title_Jurassic Park (1993), title_Sixth Sense...   
10859725  (title_Jurassic Park (1993), title_Sixth Sense...   

          antecedent support  consequent support   support  confidence  \
0                   0.176568            0.237624  0.122112    0.691589   
1                   0.237624            0.176568  0.122112    0.513889   
2                   0.176568            0.204620  0.113861    0.644860   
3                   0.204620            0.176568  0.113861    0.556452   
4                   0.331683            0.176568  0.112211    0.338308   
...                      ...                 ...       ...         ...   
10859721            0.320132            0.092409  0.090759    0.283505   
10859722            0.501650            0.099010  0.090759    0.180921   
10859723            0.343234            0.090759  0.090759    0.264423   
10859724            0.409241            0.092409  0.090759    0.221774   
10859725            0.212871            0.097360  0.090759    0.426357   

              lift  leverage  conviction  
0         2.910436  0.080156    2.471947  
1         2.910436  0.080156    1.693918  
2         3.151492  0.077732    2.239621  
3         3.151492  0.077732    1.856466  
4         1.916027  0.053647    1.244435  
...            ...       ...         ...  
10859721  3.067931  0.061176    1.266709  
10859722  1.827303  0.041091    1.100004  
10859723  2.913462  0.059607    1.236092  
10859724  2.399914  0.052941    1.166231  
10859725  4.379188  0.070034    1.573522  

[10859726 rows x 9 columns]

#### Conclusion

En esta primera aproximacion de reglas de asociacion sobre el dataset, no tenemos en cuenta el raiting que le puso cada usuario a cada pelicula. Por lo que asumimos que si la pelicula fue vista por el usuario, entonces quiere decir que algo de la misma le atrajo. 

### Reglas de asociación basado en las peliculas teniendo en cuenta el  raiting (igual o mayor a 4)

- Item: Peliculas vistas por un usuario con rating mayor o igual a 4
- I: todas las peliculas vistas por los usuarios con rating mayor o igual a 4
- Transacción: peliculas vistas por cada usuario con rating mayor o igual a 4

In [23]:
peliculas_df.head()

userId  movieId  rating  timestamp                       title  \
0           1        1     4.0  964982703            Toy Story (1995)   
12117       1     2389     2.0  964983094               Psycho (1998)   
12126       1     2395     5.0  964981093             Rushmore (1998)   
12182       1     2406     4.0  964982310  Romancing the Stone (1984)   
776         1       70     3.0  964982400  From Dusk Till Dawn (1996)   

                                            genres  
0      Adventure|Animation|Children|Comedy|Fantasy  
12117                        Crime|Horror|Thriller  
12126                                 Comedy|Drama  
12182              Action|Adventure|Comedy|Romance  
776                  Action|Comedy|Horror|Thriller

In [24]:
dummyes_mov = pd.get_dummies(peliculas_df[peliculas_df['rating']>=4][['userId','title']])
dummyes_mov = dummyes_mov.groupby('userId').sum()
dummyes_mov = clean_dataset(dummyes_mov)
dummyes_mov.head()

title_'71 (2014)  title_'Hellboy': The Seeds of Creation (2004)  \
userId                                                                    
1                      0                                              0   
2                      0                                              0   
3                      0                                              0   
4                      0                                              0   
5                      0                                              0   

        title_'Salem's Lot (2004)  title_'Til There Was You (1997)  \
userId                                                               
1                               0                                0   
2                               0                                0   
3                               0                                0   
4                               0                                0   
5                               0                                0   

        title_'burbs, The (1989)  title_(500) Days of Summer (2009)  \
userId                                                                
1                              0                                  0   
2                              0                                  0   
3                              0                                  0   
4                              0                                  0   
5                              0                                  0   

        title_*batteries not included (1987)  \
userId                                         
1                                          0   
2                                          0   
3                                          0   
4                                          0   
5                                          0   

        title_...And Justice for All (1979)  \
userId                                        
1                                         0   
2                                         0   
3                                         0   
4                                         0   
5                                         0   

        title_00 Schneider - Jagd auf Nihil Baxter (1994)  \
userId                                                      
1                                                       0   
2                                                       0   
3                                                       0   
4                                                       0   
5                                                       0   

        title_1-900 (06) (1994)  title_10 (1979)  \
userId                                             
1                             0                0   
2                             0                0   
3                             0                0   
4                             0                0   
5                             0                0   

        title_10 Cloverfield Lane (2016)  \
userId                                     
1                                      0   
2                                      0   
3                                      0   
4                                      0   
5                                      0   

        title_10 Things I Hate About You (1999)  title_10,000 BC (2008)  \
userId                                                                    
1                                             0                       0   
2                                             0                       0   
3                                             0                       0   
4                                             0                       0   
5                                             0                       0   

        title_101 Dalmatians (1996)  \
userId                                
1                                 0   
2                                 0   
3                                 0   
4  

In [25]:
from mlxtend.frequent_patterns import apriori

frequent_itemsets = apriori(dummyes_mov, min_support=0.09, use_colnames=True)
frequent_itemsets['length'] = frequent_itemsets['itemsets'].apply(lambda x: len(x))
frequent_itemsets

support                                           itemsets  length
0     0.125000               (title_2001: A Space Odyssey (1968))       1
1     0.184211                             (title_Aladdin (1992))       1
2     0.180921                               (title_Alien (1979))       1
3     0.139803                              (title_Aliens (1986))       1
4     0.093750                             (title_Amadeus (1984))       1
...        ...                                                ...     ...
1413  0.097039  (title_Star Wars: Episode V - The Empire Strik...       4
1414  0.100329  (title_Star Wars: Episode V - The Empire Strik...       4
1415  0.093750  (title_Indiana Jones and the Last Crusade (198...       5
1416  0.090461  (title_Matrix, The (1999), title_Star Wars: Ep...       5
1417  0.095395  (title_Matrix, The (1999), title_Raiders of th...       5

[1418 rows x 3 columns]

In [26]:
from mlxtend.frequent_patterns import association_rules

association_rules(frequent_itemsets, metric="confidence", min_threshold=0.01)

antecedents  \
0                                (title_Aladdin (1992))   
1                           (title_Forrest Gump (1994))   
2                          (title_Jurassic Park (1993))   
3                                (title_Aladdin (1992))   
4                                (title_Aladdin (1992))   
...                                                 ...   
6201                         (title_Matrix, The (1999))   
6202  (title_Raiders of the Lost Ark (Indiana Jones ...   
6203  (title_Star Wars: Episode VI - Return of the J...   
6204  (title_Star Wars: Episode V - The Empire Strik...   
6205  (title_Star Wars: Episode IV - A New Hope (1977))   

                                            consequents  antecedent support  \
0                           (title_Forrest Gump (1994))            0.184211   
1                                (title_Aladdin (1992))            0.407895   
2                                (title_Aladdin (1992))            0.238487   
3                          (title_Jurassic Park (1993))            0.184211   
4                         (title_Lion King, The (1994))            0.184211   
...                                                 ...                 ...   
6201  (title_Star Wars: Episode V - The Empire Strik...            0.365132   
6202  (title_Matrix, The (1999), title_Star Wars: Ep...            0.268092   
6203  (title_Matrix, The (1999), title_Star Wars: Ep...            0.246711   
6204  (title_Matrix, The (1999), title_Star Wars: Ep...            0.276316   
6205  (title_Matrix, The (1999), title_Star Wars: Ep...            0.330592   

      consequent support   support  confidence      lift  leverage  conviction  
0               0.407895  0.118421    0.642857  1.576037  0.043283    1.657895  
1               0.184211  0.118421    0.290323  1.576037  0.043283    1.149522  
2               0.184211  0.105263    0.441379  2.396059  0.061331    1.460364  
3               0.238487  0.105263    0.571429  2.396059  0.061331    1.776864  
4               0.189145  0.115132    0.625000  3.304348  0.080289    2.162281  
...                  ...       ...         ...       ...       ...         ...  
6201            0.128289  0.095395    0.261261  2.036498  0.048552    1.179998  
6202            0.131579  0.095395    0.355828  2.704294  0.060119    1.348120  
6203            0.111842  0.095395    0.386667  3.457255  0.067802    1.448084  
6204            0.100329  0.095395    0.345238  3.441062  0.067672    1.374043  
6205            0.100329  0.095395    0.288557  2.876111  0.062227    1.264573  

[6206 rows x 9 columns]

### Reglas de asociación basado género

- Item: Genero vistos por un usuario
- I: todas las generos vistos por los usuarios
- Transacción: Todos los generos vistos por cada usuario

In [15]:
genres_df = pd.DataFrame(columns = ['userId', 'Adventure',
 'Animation',
 'Children',
 'Comedy',
 'Fantasy',
 'Crime',
 'Horror',
 'Thriller',
 'Drama',
 'Action',
 'Romance',
 'Mystery',
 'War',
 'Sci-Fi',
 'Western',
 'Musical',
 'Film-Noir',
 'Documentary',
 'IMAX',
 '(no genres listed)'])
genres_df['userId'] = list(peliculas_df.groupby('userId')['userId'].groups.keys())
genres_df.head()

userId Adventure Animation Children Comedy Fantasy Crime Horror Thriller  \
0       1       NaN       NaN      NaN    NaN     NaN   NaN    NaN      NaN   
1       2       NaN       NaN      NaN    NaN     NaN   NaN    NaN      NaN   
2       3       NaN       NaN      NaN    NaN     NaN   NaN    NaN      NaN   
3       4       NaN       NaN      NaN    NaN     NaN   NaN    NaN      NaN   
4       5       NaN       NaN      NaN    NaN     NaN   NaN    NaN      NaN   

  Drama Action Romance Mystery  War Sci-Fi Western Musical Film-Noir  \
0   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
1   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
2   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
3   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
4   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   

  Documentary IMAX (no genres listed)  
0         NaN  NaN                NaN  
1         NaN  NaN                NaN  
2         NaN  NaN                NaN  
3         NaN  NaN                NaN  
4         NaN  NaN                NaN

In [16]:
dicc = {}
genres_list = []

for i, row in peliculas_df.iterrows():
    lista_genero = row['genres'].split('|')
    for each in lista_genero:
        genres_df.loc[genres_df.userId == i, each] = 1
        

genres_df.head()

userId Adventure Animation Children Comedy Fantasy Crime Horror Thriller  \
0       1         1         1        1      1       1   NaN    NaN      NaN   
1       2         1         1        1      1       1   NaN    NaN      NaN   
2       3         1         1        1      1       1   NaN    NaN      NaN   
3       4         1         1        1      1       1   NaN    NaN      NaN   
4       5         1         1        1      1       1   NaN    NaN      NaN   

  Drama Action Romance Mystery  War Sci-Fi Western Musical Film-Noir  \
0   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
1   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
2   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
3   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   
4   NaN    NaN     NaN     NaN  NaN    NaN     NaN     NaN       NaN   

  Documentary IMAX (no genres listed)  
0         NaN  NaN                NaN  
1         NaN  NaN                NaN  
2         NaN  NaN                NaN  
3         NaN  NaN                NaN  
4         NaN  NaN                NaN

In [17]:
genres_df = genres_df.fillna(0)
genres_df.head()

userId  Adventure  Animation  Children  Comedy  Fantasy  Crime  Horror  \
0       1          1          1         1       1        1      0       0   
1       2          1          1         1       1        1      0       0   
2       3          1          1         1       1        1      0       0   
3       4          1          1         1       1        1      0       0   
4       5          1          1         1       1        1      0       0   

   Thriller  Drama  Action  Romance  Mystery  War  Sci-Fi  Western  Musical  \
0         0      0       0        0        0    0       0        0        0   
1         0      0       0        0        0    0       0        0        0   
2         0      0       0        0        0    0       0        0        0   
3         0      0       0        0        0    0       0        0        0   
4         0      0       0        0        0    0       0        0        0   

   Film-Noir  Documentary  IMAX  (no genres listed)  
0          0            0     0                   0  
1          0            0     0                   0  
2          0            0     0                   0  
3          0            0     0                   0  
4          0            0     0                   0

In [18]:
genres_df.set_index('userId')

Adventure  Animation  Children  Comedy  Fantasy  Crime  Horror  \
userId                                                                   
1               1          1         1       1        1      0       0   
2               1          1         1       1        1      0       0   
3               1          1         1       1        1      0       0   
4               1          1         1       1        1      0       0   
5               1          1         1       1        1      0       0   
...           ...        ...       ...     ...      ...    ...     ...   
606             0          0         0       0        0      1       0   
607             0          0         0       0        0      1       0   
608             0          0         0       0        0      1       0   
609             0          0         0       0        0      1       0   
610             0          0         0       0        0      1       0   

        Thriller  Drama  Action  Romance  Mystery  War  Sci-Fi  Western  \
userId                                                                    
1              0      0       0        0        0    0       0        0   
2              0      0       0        0        0    0       0        0   
3              0      0       0        0        0    0       0        0   
4              0      0       0        0        0    0       0        0   
5              0      0       0        0        0    0       0        0   
...          ...    ...     ...      ...      ...  ...     ...      ...   
606            1      0       0        0        1    0       0        0   
607            1      0       0        0        1    0       0        0   
608            1      0       0        0        1    0       0        0   
609            1      0       0        0        1    0       0        0   
610            1      0       0        0        1    0       0        0   

        Musical  Film-Noir  Documentary  IMAX  (no genres listed)  
userId                                                             
1             0          0            0     0                   0  
2             0          0            0     0                   0  
3             0          0            0     0                   0  
4             0          0            0     0                   0  
5             0          0            0     0                   0  
...         ...        ...          ...   ...                 ...  
606           0          0            0     0                   0  
607           0          0            0     0                   0  
608           0          0            0     0                   0  
609           0          0            0     0                   0  
610           0          0            0     0                   0  

[610 rows x 20 columns]

In [25]:
from mlxtend.frequent_patterns import apriori


frequent_itemsets = apriori(genres_df.set_index('userId'), min_support=0.009, use_colnames=True)
frequent_itemsets['length'] = frequent_itemsets['itemsets'].apply(lambda x: len(x))
frequent_itemsets

support                                           itemsets  length
0   0.350820                                        (Adventure)       1
1   0.350820                                        (Animation)       1
2   0.350820                                         (Children)       1
3   0.436066                                           (Comedy)       1
4   0.350820                                          (Fantasy)       1
..       ...                                                ...     ...
39  0.350820          (Fantasy, Animation, Children, Adventure)       4
40  0.350820            (Comedy, Animation, Fantasy, Adventure)       4
41  0.350820             (Fantasy, Comedy, Children, Adventure)       4
42  0.350820             (Fantasy, Animation, Children, Comedy)       4
43  0.350820  (Comedy, Fantasy, Animation, Children, Adventure)       5

[44 rows x 3 columns]

In [26]:
from mlxtend.frequent_patterns import association_rules
association_rules(frequent_itemsets, metric="confidence", min_threshold=0.009)

antecedents                                consequents  \
0    (Animation)                                (Adventure)   
1    (Adventure)                                (Animation)   
2     (Children)                                (Adventure)   
3    (Adventure)                                 (Children)   
4       (Comedy)                                (Adventure)   
..           ...                                        ...   
199     (Comedy)  (Fantasy, Animation, Children, Adventure)   
200    (Fantasy)   (Comedy, Animation, Children, Adventure)   
201  (Animation)     (Fantasy, Comedy, Children, Adventure)   
202   (Children)    (Fantasy, Comedy, Animation, Adventure)   
203  (Adventure)     (Fantasy, Comedy, Animation, Children)   

     antecedent support  consequent support  support  confidence      lift  \
0              0.350820             0.35082  0.35082    1.000000  2.850467   
1              0.350820             0.35082  0.35082    1.000000  2.850467   
2              0.350820             0.35082  0.35082    1.000000  2.850467   
3              0.350820             0.35082  0.35082    1.000000  2.850467   
4              0.436066             0.35082  0.35082    0.804511  2.293233   
..                  ...                 ...      ...         ...       ...   
199            0.436066             0.35082  0.35082    0.804511  2.293233   
200            0.350820             0.35082  0.35082    1.000000  2.850467   
201            0.350820             0.35082  0.35082    1.000000  2.850467   
202            0.350820             0.35082  0.35082    1.000000  2.850467   
203            0.350820             0.35082  0.35082    1.000000  2.850467   

     leverage  conviction  
0    0.227745         inf  
1    0.227745         inf  
2    0.227745         inf  
3    0.227745         inf  
4    0.197839    3.320807  
..        ...         ...  
199  0.197839    3.320807  
200  0.227745         inf  
201  0.227745         inf  
202  0.227745         inf  
203  0.227745         inf  

[204 rows x 9 columns]